In [1]:
import os
import math
import numpy as np
from numpy import linalg as la
from statistics import mean 
import pandas as pd
import operator
from operator import itemgetter
from collections import defaultdict
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
import json
os.getcwd()
os.chdir('C:\\Users\\Kristal\\Desktop\\CSC_575 Homework\\Final Project')
os.getcwd()

'C:\\Users\\Kristal\\Desktop\\CSC_575 Homework\\Final Project'

VIDEO DESCRIPTION OF NOTEBOOK FOUND HERE: https://www.youtube.com/watch?v=hPpjNzZKh6o&feature=youtu.be

# Reading in Data and Creation of Inverted Index

In [2]:
stop_words = nltk.corpus.stopwords.words('english')

Stopwords for the trump data set are taken from the nltk stopwords corpus. The trump data set consists of a 7375 tweets over the course of two years.

In [3]:
whole_tweets_df = pd.read_csv('Donald-Tweets!.csv')
tweets_df = whole_tweets_df['Tweet_Text']
tweets_df[0]

'Today we express our deepest gratitude to all those who have served in our armed forces. #ThankAVet https://t.co/wPk7QWpK8Z'

In [4]:
def token_filter_stem(doc, stop_words):                  #a function that tokenizes, filters, and stems a document
    extra_stoppers = ['http',":",".","!","#",",","@","I",'-',"''","``",]     #extra stop words that occur in too many documents to be useful
    words = word_tokenize(doc)
    filtered_words = [w for w in words if w not in stop_words]
    ps = PorterStemmer()
    stemmed = [ps.stem(w) for w in filtered_words]
    stemmed_df = []         # a list that will contain 2 value lists that contain the stemmed token and its TF for that document
    for s in set(stemmed):
        if s not in extra_stoppers:
            if s.startswith('//t') == False:           #removes partial links being used as inverted index tokens
                stemmed_df.append([s,stemmed.count(s)])
            
    return stemmed_df

In [5]:
stemtest = token_filter_stem(tweets_df[0], stop_words)
print(stemtest)

[['express', 1], ['arm', 1], ['serv', 1], ['gratitud', 1], ['thankavet', 1], ['forc', 1], ['deepest', 1], ['today', 1]]


As seen above and using 1 tweet for an example, our token_filter_stem function works and provides us with the above tokens and their TF for that document. This token_filter_stem function utilizes the word_tokenize function to tokenize the document from nltk as well as the PorterStemmer function from nltk to stem the tokens given by word_tokenize.

In [6]:
def inverted_index_creation(docDF, stop_words):
    #inver_index[key][0] = doc frequency
    #inver_index[key][1] = idf
    #inver_index[key][2] = postings list - a list 2 digit lists in the format[docID,termfrequency]
    inver_index = defaultdict(list)
    docID = 1
    numDocs = 0
    doc_length_dict = {}
    for i in docDF:
        numDocs+=1
        doc_length_dict[docID]=0
        stemmed = token_filter_stem(i, stop_words)  #filters,stems, and tokenizes the document given - returns list of tokens
        for s in stemmed:
            if s[0] not in inver_index.keys():      #creates a new empty token in our index if that token doesn't exist yet
                inver_index[s[0]]=[0,0,[]]
            inver_index[s[0]][2].append([docID,s[1]])  # adds a posting to that token in our inver_index
        docID+=1
    
    for t in inver_index.keys():                               #computes the IDF for all tokens in inver_index
        m = len(inver_index[t][2])
        idf = math.log(numDocs/m,2)
        inver_index[t][1]=idf                                 #idf for token added to inverted index
        inver_index[t][0]=m                                   #document freqency m added to inverted index
        
    
    
    for y in inver_index.keys():                              #computes vector lengths for all documents in inver_index
        idf_weight = inver_index[y][1] 
        for tokOccur in inver_index[y][2]: 
            dtc = tokOccur[1]                               #dtc stands for doc-term-count
            dLength = (idf_weight*dtc)**2
            doc_length_dict[tokOccur[0]]+=dLength           #increment vector length
            
            
            
    for d in doc_length_dict.keys():
         doc_length_dict[d] = math.sqrt(doc_length_dict[d])  #this gives us document vector norm
    
    
    
         
            
    return inver_index, doc_length_dict  #returns our inverted index and a dictionary of document lengths(normalized)
            

In [7]:
tweets_index, tweets_lengths = inverted_index_creation(tweets_df,stop_words)
for key in tweets_index:
    print(key,tweets_index[key])
    print()
print("---------------------------------------")
for key in tweets_lengths:
    print(key,tweets_lengths[key])
    print()

express [4, 10.848427334023928, [[1, 1], [784, 1], [2229, 1], [3143, 1]]]

arm [9, 9.678502332581616, [[1, 1], [793, 1], [864, 1], [1488, 1], [1571, 1], [1948, 1], [3931, 1], [6919, 1], [7209, 1]]]

serv [15, 8.94153673841541, [[1, 1], [75, 1], [366, 1], [872, 1], [1174, 1], [1532, 1], [1943, 1], [2889, 1], [3509, 1], [3882, 1], [4007, 1], [4909, 1], [6558, 2], [7063, 1], [7288, 1]]]

gratitud [2, 11.84842733402393, [[1, 1], [658, 1]]]

thankavet [2, 11.84842733402393, [[1, 1], [3509, 1]]]

forc [20, 8.526499239136566, [[1, 1], [62, 1], [78, 1], [379, 1], [594, 1], [740, 1], [780, 1], [896, 1], [959, 1], [1541, 1], [1543, 1], [1933, 1], [2316, 1], [3113, 1], [5076, 1], [5552, 1], [5567, 1], [6521, 1], [6605, 1], [7338, 1]]]

deepest [4, 10.848427334023928, [[1, 1], [658, 1], [667, 1], [6631, 1]]]

today [195, 5.241097020274317, [[1, 1], [18, 1], [19, 1], [20, 1], [26, 1], [71, 1], [105, 1], [114, 1], [158, 1], [225, 1], [252, 1], [360, 1], [419, 1], [448, 1], [449, 1], [452, 1], [460, 

Shown above: Using the inverted_index_creation function above I am able to successfully create an inverted index that uses tokens as our keys and has a list of information about that token as well the posting information that goes with it. I also return a dictionary with document ID's and their corresponding document length.

In [8]:
def save_index(index,filename):
    with open(filename, 'w') as fp:
        json.dump(index, fp)

In [9]:
save_index(tweets_index,'Trump_Tweet_Index.json')
save_index(tweets_lengths, 'Trump_Tweet_doclengths.json')

In [10]:
def retrieve_index(filename):
    with open(filename, 'r') as fp:
        data = json.load(fp)
    return data

In [11]:
tweets_index_reloaded = retrieve_index('Trump_Tweet_Index.json')
tweets_lengths_reloaded = retrieve_index('Trump_Tweet_doclengths.json')
for key in tweets_index_reloaded:
    print(key,tweets_index_reloaded[key])
    print()
print("---------------------------------------")
for key in tweets_lengths_reloaded:
    print(key,tweets_lengths_reloaded[key])
    print()

express [4, 10.848427334023928, [[1, 1], [784, 1], [2229, 1], [3143, 1]]]

arm [9, 9.678502332581616, [[1, 1], [793, 1], [864, 1], [1488, 1], [1571, 1], [1948, 1], [3931, 1], [6919, 1], [7209, 1]]]

serv [15, 8.94153673841541, [[1, 1], [75, 1], [366, 1], [872, 1], [1174, 1], [1532, 1], [1943, 1], [2889, 1], [3509, 1], [3882, 1], [4007, 1], [4909, 1], [6558, 2], [7063, 1], [7288, 1]]]

gratitud [2, 11.84842733402393, [[1, 1], [658, 1]]]

thankavet [2, 11.84842733402393, [[1, 1], [3509, 1]]]

forc [20, 8.526499239136566, [[1, 1], [62, 1], [78, 1], [379, 1], [594, 1], [740, 1], [780, 1], [896, 1], [959, 1], [1541, 1], [1543, 1], [1933, 1], [2316, 1], [3113, 1], [5076, 1], [5552, 1], [5567, 1], [6521, 1], [6605, 1], [7338, 1]]]

deepest [4, 10.848427334023928, [[1, 1], [658, 1], [667, 1], [6631, 1]]]

today [195, 5.241097020274317, [[1, 1], [18, 1], [19, 1], [20, 1], [26, 1], [71, 1], [105, 1], [114, 1], [158, 1], [225, 1], [252, 1], [360, 1], [419, 1], [448, 1], [449, 1], [452, 1], [460, 

As shown above, the save_index function and retrieve_index function allow us to store our inverted index dictionary as a json file and retrieve it so that we do not need to create the inverted index from scratch each time we want to perform a query

# Performing a Query

In [12]:
def search_query(qString, index, doc_index, dataframe, stop_words, n_results=10,verbose=True):
                #string  #invind #doclengths #textdata #stopwords  #results defaults 10
    stemmed = token_filter_stem(qString.strip(), stop_words)   #stems,tokens, and filters the query and returns a list of lists [token,tf]
    retrieved = {}           #a dictionary to store all retrieved documents
    vecWeights = []
    for s in stemmed:                        #for every token in the query
        if s[0] in index.keys() and index[s[0]] != []:
            idf = index[s[0]][1]              #look up idf in inver_index
            term_count = s[1]                 #look up the term frequency of query
            weight = idf*term_count           #calculates weight of the term in the query
            vecWeights.append(weight)
            token_list = index[s[0]][2]       #looks up the list of postings in the inver_index for a token s[0] in the query
            for occ in token_list:            #for every posting
                doc = occ[0]                  #document id from posting
                count = occ[1]                #tf within document from posting
                if doc not in retrieved.keys():
                    retrieved[doc] = 0
                retrieved[doc]+=weight*idf*count  #this is incrementing until for that document we have the dot-product of doc and query
            
    qlength = la.norm(vecWeights) 
    
    for d in retrieved.keys():                              #calculates scores for each retrieved document
        score = retrieved[d]   
        doclength = doc_index[d]     #look this up as it was already calculated
        retrieved[d] = score/(qlength*doclength)
    sorted_docs = sorted(retrieved.items(), key=operator.itemgetter(1),reverse=True)
    
    if verbose == True:                           #serves as a default printed format of returned results. Can be disabled.
        topN_results = sorted_docs[0:n_results]
        print("Top ",n_results," Query Results")
        print("----------------------------------")
        if isinstance(dataframe, pd.Series):
            for k in topN_results:
                print("Document:",k[0],"Cosine Sim:",k[1],"\n",dataframe[k[0]-1])
                print("----------------------------------")
        else:
            for k in topN_results:
                print("Document:",k[0],"Cosine Sim:",k[1],"\n",dataframe[k[0]])
                print("----------------------------------")
                       
    sorted_list = []                              #instantiates a list that stores N documents with the higest cosine sim shown first
    for u in sorted_docs[0:n_results]:
        if isinstance(dataframe, pd.Series):      #handles the appending if of the document text if you used a pandas series
            doc_doctext = [u[0],dataframe[u[0]-1]]
            sorted_list.append(doc_doctext)
        else:
            doc_doctext = [u[0],dataframe[u[0]]]  #handles the appending of the document text if you used anything else
            sorted_list.append(doc_doctext)
    return sorted_list                            #returns a sorted list of documents

In [13]:
search_query("obama", tweets_index, tweets_lengths, tweets_df, stop_words, n_results=10,verbose=True)

Top  10  Query Results
----------------------------------
Document: 4540 Cosine Sim: 0.5033564929280571 
 What is Obama thinking? https://t.co/YWINe9t8w3
----------------------------------
Document: 70 Cosine Sim: 0.387701514449314 
 "The Clinton Campaign at Obama Justice" #DrainTheSwamp
https://t.co/LZkvFc071z
----------------------------------
Document: 825 Cosine Sim: 0.3825402487975364 
 Russia took Crimea during the so-called Obama years. Who wouldnt know this and why does Obama get a free pass?
----------------------------------
Document: 4394 Cosine Sim: 0.34098661204265235 
 Obama said in his speech that Muslims are our sports heroes. What sport is he talking about, and who? Is Obama profiling?
----------------------------------
Document: 903 Cosine Sim: 0.3201433345385225 
 President Obama &amp; Putin fail to reach deal on Syria - so what else is new? Obama is not a natural deal maker. Only makes bad deals!
----------------------------------
Document: 1178 Cosine Sim: 0.315123

[[4540, 'What is Obama thinking? https://t.co/YWINe9t8w3'],
 [70,
  '"The Clinton Campaign at Obama Justice" #DrainTheSwamp\nhttps://t.co/LZkvFc071z'],
 [825,
  'Russia took Crimea during the so-called Obama years. Who wouldnt know this and why does Obama get a free pass?'],
 [4394,
  'Obama said in his speech that Muslims are our sports heroes. What sport is he talking about, and who? Is Obama profiling?'],
 [903,
  'President Obama &amp; Putin fail to reach deal on Syria - so what else is new? Obama is not a natural deal maker. Only makes bad deals!'],
 [1178,
  'President Obama should ask the DNC about how they rigged the election against Bernie.'],
 [3596, 'Obamas deal vs. Trumps deals- https://t.co/UpQ3LkUUpm'],
 [252,
  'RT @TeamTrump: When Obama took office in 2009 employer-provided premiums cost $13,375. Today they are $18,142. Thanks, Obama.'],
 [4434, 'Wonder if Obama will ever say RADICAL ISLAMIC TERRORIST?'],
 [512,
  'Obama and Clinton told the same lie to sell #ObamaCare.

Here is a search on the term "obama" and the top 10 results for that search. As can be seen, all the documents contain Obama and in this case seem relevant to our search. Additionally, the returned documents have been sorted by their Cosine similarity with the highest cosine similarity document appearing first, followed by the next highest, etc.

# Testing our Search Engine with Benchmark Data

In [14]:
with open('TIME_docs.txt','r') as reader:
    benchmark_docs = []         # a list to store all our concatenated benchmark documents
    benchmark_docs_id = {}
    docID = 1
    doc = str("")                               
    doc_pieces = []             # a list of all the string fragments that will make up one document, is reset on doc completion
    seper = " "                 # the separator when joining doc pieces so that there is a space between the two words
    delim = "*"                 # a delimiter that when read in a line signifies that the doc pieces should be joined and added to benchmark_docs
    for line in reader:
        if delim in line:
            doc = seper.join(doc_pieces)
            doc = doc.strip()  #strips leading and ending spaces of new document
            benchmark_docs.append(doc)
            doc_pieces = []
            continue
           
        fixed_line = line.rstrip()  #strips newline characters
        doc_pieces.append(fixed_line) #adds a fixed line to the document pieces list
    benchmark_docs.pop(0)             #removes an initial empty list that is generated by the first delimiter found in the first row
    
    for docy in benchmark_docs:       #additional code section added - adds benchmark doc to a dictionary benchmark_doc_id's
        benchmark_docs_id[docID] = docy
        docID+=1

print(benchmark_docs_id[2])

RUSSIA WHO'S IN CHARGE HERE ? IT WAS IN 1954 THAT NIKITA  KHRUSHCHEV LAUNCHED HIS GRANDIOSE " VIRGIN LANDS " GAMBLE . PART OF THE  PLAN WAS TO PLOW UP 32 MILLION ACRES OF MARGINAL LAND IN KAZAKHSTAN,  AND SETTLE IT WITH COMMUNIST " PIONEERS, " WHO WERE TO PLANT AND  PRODUCE HUGE QUANTITIES OF DESPERATELY NEEDED GRAIN WITHIN TWO YEARS .  NIKITA'S SCHEME FLOPPED . THERE WAS NOT ENOUGH RAINFALL, AND THE  PIONEERS DID NOT TAKE TO TRACTOR LIFE ON THE BLEAK FRONTIER . EXCEPT  FOR 1958, EACH HARVEST HAS BEEN LOWER THAN THE PREVIOUS YEAR'S . WORST  YEAR OF ALL WAS 1962, WHEN THE VIRGIN LANDS DELIVERED ONLY HALF THEIR  QUOTAS . NATURALLY, KHRUSHCHEV TAKES NONE OF THE BLAME FOR THE FIASCO .  THREE YEARS AGO HE FOUND A SCAPEGOAT IN KAZAKHSTAN PARTY BOSS NIKOLAI  BELYAEV, FIRED HIM FOR HIS " ERRORS . " LAST WEEK BELYAEV'S SUCCESSOR,  DINMUKHAMED KUNAEV, WAS SIMILARLY BOUNCED FOR " LAPSES " IN HIS WORK .  FOR GOOD MEASURE, MOSCOW ALSO PURGED THE FORMER PREMIER OF THE  TERRITORY FROM THE LOCAL PARTY

In [15]:
with open('TIME_stopwords.txt','r') as reader:   #Reads in all the stop words for the benchmark dataset
    benchmark_stops = []
    for line in reader:
        fixed_line2 = line.rstrip()
        if fixed_line2 is not "":
            benchmark_stops.append(fixed_line2)
print(benchmark_stops)

['A', 'ABOUT', 'ABOVE', 'ACROSS', 'ACTUALLY', 'ADD', 'ADDED', 'AFTER', 'AGAIN', 'AGAINST', 'AGO', 'ALL', 'ALMOST', 'ALONG', 'ALREADY', 'ALSO', 'ALTHOUGH', 'ALWAYS', 'AM', 'AMONG', 'AN', 'AND', 'ANOTHER', 'ANY', 'ANYONE', 'ARE', 'AROUND', 'AS', 'ASKED', 'AT', 'B', 'BACK', 'BAD', 'BE', 'BECAME', 'BECAUSE', 'BECOME', 'BEEN', 'BEFORE', 'BEGAN', 'BEHIND', 'BEING', 'BEST', 'BETTER', 'BETWEEN', 'BIG', 'BIGGEST', 'BOTH', 'BROUGHT', 'BUT', 'BY', 'C', 'CALLED', 'CAME', 'CAN', 'CANNOT', 'CENT', 'COME', 'COMPLETE', 'CONTINUED', 'COULD', 'D', 'DAY', 'DECIDED', 'DECLARED', 'DESPITE', 'DID', 'DO', 'DOES', 'DOWN', 'DURING', 'E', 'EACH', 'EARLY', 'EIGHT', 'ENOUGH', 'ENTIRE', 'EP', 'ETC', 'EVEN', 'EVER', 'EVERY', 'EVERYTHING', 'F', 'FACE', 'FACED', 'FACT', 'FAILED', 'FAR', 'FELL', 'FEW', 'FINALLY', 'FIND', 'FIRST', 'FIVE', 'FOR', 'FOUND', 'FOUR', 'FROM', 'G', 'GAVE', 'GET', 'GIVE', 'GIVEN', 'GO', 'GOING', 'GOOD', 'GOT', 'H', 'HAD', 'HAS', 'HAVE', 'HAVING', 'HE', 'HELD', 'HER', 'HERE', 'HIM', 'HIMSELF', 

In [16]:
with open('TIME_queries.txt','r') as reader:  #works almost the same as the benchmark document reader above - see comments there
    benchmark_queries = []
    benchmark_queries_id = {}
    query = str("")
    query_pieces = []
    seper = " "
    delim = "*"
    queryID=1
    for line in reader:
        if delim in line:
            query = seper.join(query_pieces)
            query = query.strip()
            benchmark_queries.append(query)
            query_pieces = []
            continue
           
        fixed_line3 = line.rstrip()
        query_pieces.append(fixed_line3)
    benchmark_queries.pop(0)
    
    
    for que in benchmark_queries:       #additional code section added - adds benchmark query to a dictionary benchmark_queries_id
        benchmark_queries_id[queryID] = que
        queryID+=1
print(benchmark_queries_id[1])

KENNEDY ADMINISTRATION PRESSURE ON NGO DINH DIEM TO STOP  SUPPRESSING THE BUDDHISTS .


In [17]:
with open('TIME_relevance.txt','r') as reader:   #reads in our relevance information for each of the benchmark queries
    benchmark_rels = []                          #a list of lists that each store the query ID and the list of relevant documents
    for line in reader:
        fixed_line4 = line.rstrip()              #remove \n
        if fixed_line4 is not "":
            rel_docs = []                        # a list to be appended to of all the relevant documents given in that line
            rel_docs_strings = fixed_line4.split()[1:] # gives a list of all the relevant documents in string format
            temp_ID = int(fixed_line4.split()[0])      # gives the query ID by looking at the first element of the split line
            for i in rel_docs_strings:                 #appends each document ID in integer form to one list - rel_docs
                rel_docs.append(int(i))
            benchmark_rels.append([temp_ID,rel_docs])  #appends the query ID and doc list for that ID to the master list
print(benchmark_rels[8])

[9, [61, 155, 156, 242, 269, 315, 339, 358]]


As seen in the cells above I was able to read in all the benchmark data for the TIME dataset in a format usable by my search engine. The documents are in a dictionary called benchmark_docs_id, the stop words are in a list called benchmark_stops, the queries are in a dictionary called benchmark_queries_id, and the relevance information for each query is in a list of lists.

In [18]:
benchmark_index,benchmark_lengths = inverted_index_creation(benchmark_docs,benchmark_stops)
for key in benchmark_index:
    print(key,benchmark_index[key])
    print()
print("---------------------------------------")
for key in benchmark_lengths:
    print(key,benchmark_lengths[key])
    print()

strength [34, 3.63705101186961, [[1, 1], [33, 1], [37, 1], [40, 1], [47, 2], [49, 1], [53, 1], [71, 1], [81, 1], [100, 1], [134, 1], [142, 1], [168, 1], [185, 1], [211, 1], [225, 1], [228, 1], [236, 1], [244, 1], [245, 1], [283, 1], [285, 1], [290, 1], [309, 1], [325, 1], [333, 1], [343, 1], [349, 3], [350, 2], [352, 1], [371, 1], [382, 1], [412, 1], [413, 1]]]

polari [15, 4.817623257511431, [[1, 7], [23, 2], [38, 4], [47, 1], [54, 1], [89, 5], [135, 2], [148, 1], [157, 5], [228, 1], [247, 1], [254, 2], [272, 1], [360, 1], [402, 1]]]

retali [11, 5.2650822344826524, [[1, 1], [38, 1], [61, 1], [94, 1], [115, 1], [135, 1], [193, 1], [194, 1], [210, 1], [326, 1], [402, 1]]]

saw [22, 4.2650822344826524, [[1, 1], [5, 1], [47, 1], [51, 1], [69, 1], [70, 1], [72, 1], [86, 1], [93, 1], [99, 1], [100, 2], [117, 1], [122, 1], [163, 1], [203, 1], [294, 1], [318, 1], [337, 1], [343, 1], [370, 1], [374, 1], [382, 1]]]

neck [9, 5.554588851677638, [[1, 1], [12, 1], [126, 1], [147, 1], [156, 1], [2

Above is the inverted index for our benchmark dataset and it's corresponding dictionary of document lengths. It looks like our inverted index constructor is working well on a set of data other than the Trump Tweet data above.

In [19]:
save_index(benchmark_index,'TIME_Benchmark_Index.json')
save_index(benchmark_lengths, 'TIME_Benchmark_doclengths.json')

Here are the json files for the inverted index and document length dicitionaries were saved. These will be included with the project so you do not need to construct the inverted indexes yourself.

In [20]:
query_tobe_searched = benchmark_queries_id[1]
search_query(query_tobe_searched, benchmark_index, benchmark_lengths, benchmark_docs_id, benchmark_stops, n_results=5,verbose=True)

Top  5  Query Results
----------------------------------
Document: 308 Cosine Sim: 0.3761631597012484 
 SOUTH VIET NAM THE BUDDHIST CRISIS IN SAIGON'S HUGE XA  LOI PAGODA, BUDDHIST MONKS AND NUNS WERE HOLDING A 48-HOUR HUNGER  STRIKE AGAINST THE REGIME OF SOUTH VIET NAM'S PRESIDENT NGO DINH DIEM .  EXPECTING TROUBLE, POLICE SEALED OFF NEARBY STREETS WITH BARBED WIRE .  TO PREVENT A REPETITION OF THE RITUALISTIC SUICIDE LAST MONTH, WHEN A  PROTESTING BUDDHIST MONK BURNED HIMSELF TO DEATH ON A SAIGON STREET  CORNER, TWO FIRE TRUCKS WERE ON HAND . SUDDENLY, ABOUT 500  SAFFRON-ROBED BUDDHIST PRIESTS, LAYMEN AND WOMEN EMERGED FROM A NEARBY  ALLEY AND STARTED TO RUN TOWARD THE PAGODA TO JOIN THEIR FASTING  FELLOW-BUDDHISTS . STYMIED BY WIRE AND POLICE, THE DEMONSTRATORS SAT  DOWN IN THE MIDDLE OF THE STREET . RIOT SQUADS ARRIVED . ARMED WITH A  WALKIE-TALKIE RADIO, TWO SPORT-SHIRTED AMERICAN C.I.A . MEN DELIVERED A  RUNNING COMMENTARY ON EVENTS TO HEADQUARTERS . A MONK WITH A PORTABLE  LOUDS

[[308,
  'SOUTH VIET NAM THE BUDDHIST CRISIS IN SAIGON\'S HUGE XA  LOI PAGODA, BUDDHIST MONKS AND NUNS WERE HOLDING A 48-HOUR HUNGER  STRIKE AGAINST THE REGIME OF SOUTH VIET NAM\'S PRESIDENT NGO DINH DIEM .  EXPECTING TROUBLE, POLICE SEALED OFF NEARBY STREETS WITH BARBED WIRE .  TO PREVENT A REPETITION OF THE RITUALISTIC SUICIDE LAST MONTH, WHEN A  PROTESTING BUDDHIST MONK BURNED HIMSELF TO DEATH ON A SAIGON STREET  CORNER, TWO FIRE TRUCKS WERE ON HAND . SUDDENLY, ABOUT 500  SAFFRON-ROBED BUDDHIST PRIESTS, LAYMEN AND WOMEN EMERGED FROM A NEARBY  ALLEY AND STARTED TO RUN TOWARD THE PAGODA TO JOIN THEIR FASTING  FELLOW-BUDDHISTS . STYMIED BY WIRE AND POLICE, THE DEMONSTRATORS SAT  DOWN IN THE MIDDLE OF THE STREET . RIOT SQUADS ARRIVED . ARMED WITH A  WALKIE-TALKIE RADIO, TWO SPORT-SHIRTED AMERICAN C.I.A . MEN DELIVERED A  RUNNING COMMENTARY ON EVENTS TO HEADQUARTERS . A MONK WITH A PORTABLE  LOUDSPEAKER REPEATED : " WE HAVE BEEN DECEIVED MANY TIMES AND WE NO  LONGER HAVE ANY FAITH IN THE

Above are the results based on the first benchmark query that was supplied to us with the TIME dataset. Just looking at the document id's and knowing that the relevant documents for this query were: 268 288 304 308 323 326 334 we can see that 3 of the 5 documents returned were relevant. Not bad. However, we should calculate the precision and recall for this query to really see how it is performing.

In [21]:
def recall_precision_calc(retrieved, benchmark_relevance, queryID,verbose=True):
    nret_docs = len(retrieved)                           #number of retrieved documents
    nrel_docs = len(benchmark_relevance[int(queryID)-1][1])   #number of relevant documents for the given query
    rel_docs = 0                                              #count of relevant documents found
    for k in retrieved:
        if k[0] in benchmark_relevance[int(queryID)-1][1]:    #if the docid(k[0]) is found in the list of relevant document ID's for that query
            rel_docs+=1                                       #increment relevant docs found by 1
    recall = rel_docs/nrel_docs                               #relevant docs divided by total number of relevant docs
    precision = rel_docs/nret_docs                            #relevant docs divdided by number of documents that were returned
    if verbose==True:                                         
        print("After ",nret_docs," returned documents:")     #An optional printer that displayed recall and precision
        print("Recall is ",recall)
        print("Precision is ",precision)
        print("------------------------------------------------------------------")
    return recall, precision                                 #returns recall and precision

In [22]:
query_tobe_searched = benchmark_queries_id[1]
query_results = search_query(query_tobe_searched, benchmark_index, benchmark_lengths, benchmark_docs_id, benchmark_stops, n_results=5,verbose=False)
recall_precision_calc(query_results, benchmark_rels, 1)

After  5  returned documents:
Recall is  0.42857142857142855
Precision is  0.6
------------------------------------------------------------------


(0.42857142857142855, 0.6)

Calculating the precision and recall for our first benchmark query we find that recall is ~.43 and precision is .6. Since we found 3 of the 5 documents that value for precision sounds exactly correct. However, what if we wanted to keep searching until we have found all relevant documents to get a more accurate precision and recall?

In [23]:
def prec_recall_overN(queryNumber, verbose2=True):
    prec_list = []                             #a list that stores precisions based on number of retrieved docs
    prev_recall=0                              #the recall value of the previous query
    recall=0                                   #the recall value of the current query
    firstrun=0                                 #a variable that acts as a "first-pass" detector and counts up until loop completes
    while recall!=1:                           #we know if recall is 1 then we have found all our docs, can stop
        retrieved_docs = search_query(benchmark_queries_id[queryNumber],benchmark_index,benchmark_lengths, benchmark_docs_id, benchmark_stops,firstrun+1,verbose=False)
        recall, precision = recall_precision_calc(retrieved_docs, benchmark_rels, queryNumber,verbose2)  #calculates recall and precision for retrieved docs
        if precision==1 and firstrun==0:        #first pass detection for if first value is relevant to add precision to list
            prec_list.append(precision)
            prev_recall = recall
            firstrun+=1
        elif prev_recall != recall:     #if the previous recall is != to recall, we know that a relevant document was found and should append precision
            prec_list.append(precision)
            prev_recall = recall
            firstrun+=1
        elif firstrun==30:          #if the recall never reaches 1 and documents are not found - exit after 30 docs retrieved
            recall=1
            firstrun+=1
        else:                    #catch-all
            firstrun+=1
            continue
    if prec_list == []:          #if no relevant documents are found return 0 for precision
        return 0
    else:
        return mean(prec_list)  #return the average of all the precisions for that query
        
prec_recall_overN(1,True)    

After  1  returned documents:
Recall is  0.14285714285714285
Precision is  1.0
------------------------------------------------------------------
After  2  returned documents:
Recall is  0.14285714285714285
Precision is  0.5
------------------------------------------------------------------
After  3  returned documents:
Recall is  0.14285714285714285
Precision is  0.3333333333333333
------------------------------------------------------------------
After  4  returned documents:
Recall is  0.2857142857142857
Precision is  0.5
------------------------------------------------------------------
After  5  returned documents:
Recall is  0.42857142857142855
Precision is  0.6
------------------------------------------------------------------
After  6  returned documents:
Recall is  0.5714285714285714
Precision is  0.6666666666666666
------------------------------------------------------------------
After  7  returned documents:
Recall is  0.7142857142857143
Precision is  0.7142857142857143
---

0.704421768707483

The above set of precision and recall tests show the precision and recalls values over a range from 1-10 retrieved documents for query 1. It took a total 10 returned documents to find all 7 relevant documents for that query which resulting in an average precision value of .7. This is great, but what if we wanted to calculate our Mean Average Precision across all queries?

In [24]:
def MAP_calc(queryData):
    c=1
    aveprec_list = []                                 #a list that store the average precision for each query
    for i in queryData:                               #for every relevance query we have
        aveprec = prec_recall_overN(i[0],verbose2=False)   #returns the average precision for that query
        aveprec_list.append(aveprec)
        print("Query ",c," Complete")
        c+=1
    print("The Mean Average Precision(MAP) across all queries is",mean(aveprec_list))

MAP_calc(benchmark_rels)

Query  1  Complete
Query  2  Complete
Query  3  Complete
Query  4  Complete
Query  5  Complete
Query  6  Complete
Query  7  Complete
Query  8  Complete
Query  9  Complete
Query  10  Complete
Query  11  Complete
Query  12  Complete
Query  13  Complete
Query  14  Complete
Query  15  Complete
Query  16  Complete
Query  17  Complete
Query  18  Complete
Query  19  Complete
Query  20  Complete
Query  21  Complete
Query  22  Complete
Query  23  Complete
Query  24  Complete
Query  25  Complete
Query  26  Complete
Query  27  Complete
Query  28  Complete
Query  29  Complete
Query  30  Complete
Query  31  Complete
Query  32  Complete
Query  33  Complete
Query  34  Complete
Query  35  Complete
Query  36  Complete
Query  37  Complete
Query  38  Complete
Query  39  Complete
Query  40  Complete
Query  41  Complete
Query  42  Complete
Query  43  Complete
Query  44  Complete
Query  45  Complete
Query  46  Complete
Query  47  Complete
Query  48  Complete
Query  49  Complete
Query  50  Complete
Query  51

Running every single relevance query we were given, our Mean Average Precision(MAP) is ~.63 which means the search engine described above is performing quite well on the TIME benchmark dataset.

# Finishing Touches and Summary

Above I was shown that I am capable of succesfully constructing an inverted index constructor for both our Trump data and our TIME benchmark data. For both of these datasets the inverted indexes and  their correspoding document length dictionaries were able to be successfully saved into json files and also retrieved for use if necessary to avoid reconstructing the entire index. After that, I developed a search function that can look over the inverted index for a set of documents and retrieve a list of those documents that is ranked by their cosine similarity to the user query. To ensure the search engine was performing well, I loaded in all the parts of the benchmark Time dataset to see how well my search engine was really performing through the use of benchmark queries. I developed a function to calculate the precision and recall based on the documents returned and the given relevance information. With this done, I then developed a function that can, return a higher quality precision metric by always using the number of documents needed to find all relevant documents for that query then averaging the precision. Finally, I wrote a function that calculated Mean Average Precision(MAP) across all queries to get an even better look at on average how precise my search engine actually is.

Down below is a small program to search through the Trump tweet database based on a query you provide. Please let me know if you find anything hilarious! :)

In [25]:
#RUN ME IF YOU WANT TO PERFORM YOUR OWN QUERY ON THE TWEET DATABASE
print('Hello!, welcome to the Trump Tweet Database')
print()

query = input("What would you like to search for? ")
numRes = int(input("How many results would you like?(Please enter a whole integer) "))
search_query(query, tweets_index, tweets_lengths, tweets_df, stop_words, n_results=numRes,verbose=True)

    

Hello!, welcome to the Trump Tweet Database

What would you like to search for? obama
How many results would you like?(Please enter a whole integer) 15
Top  15  Query Results
----------------------------------
Document: 4540 Cosine Sim: 0.5033564929280571 
 What is Obama thinking? https://t.co/YWINe9t8w3
----------------------------------
Document: 70 Cosine Sim: 0.387701514449314 
 "The Clinton Campaign at Obama Justice" #DrainTheSwamp
https://t.co/LZkvFc071z
----------------------------------
Document: 825 Cosine Sim: 0.3825402487975364 
 Russia took Crimea during the so-called Obama years. Who wouldnt know this and why does Obama get a free pass?
----------------------------------
Document: 4394 Cosine Sim: 0.34098661204265235 
 Obama said in his speech that Muslims are our sports heroes. What sport is he talking about, and who? Is Obama profiling?
----------------------------------
Document: 903 Cosine Sim: 0.3201433345385225 
 President Obama &amp; Putin fail to reach deal on Syri

[[4540, 'What is Obama thinking? https://t.co/YWINe9t8w3'],
 [70,
  '"The Clinton Campaign at Obama Justice" #DrainTheSwamp\nhttps://t.co/LZkvFc071z'],
 [825,
  'Russia took Crimea during the so-called Obama years. Who wouldnt know this and why does Obama get a free pass?'],
 [4394,
  'Obama said in his speech that Muslims are our sports heroes. What sport is he talking about, and who? Is Obama profiling?'],
 [903,
  'President Obama &amp; Putin fail to reach deal on Syria - so what else is new? Obama is not a natural deal maker. Only makes bad deals!'],
 [1178,
  'President Obama should ask the DNC about how they rigged the election against Bernie.'],
 [3596, 'Obamas deal vs. Trumps deals- https://t.co/UpQ3LkUUpm'],
 [252,
  'RT @TeamTrump: When Obama took office in 2009 employer-provided premiums cost $13,375. Today they are $18,142. Thanks, Obama.'],
 [4434, 'Wonder if Obama will ever say RADICAL ISLAMIC TERRORIST?'],
 [512,
  'Obama and Clinton told the same lie to sell #ObamaCare.